In [399]:
import numpy as np
import matplotlib.pyplot as plt
import json
import pandas as pd
from pandas import read_csv
from sklearn.utils import shuffle

In [400]:
#lade einfache Daten und wandle in einen Dataframe um
with open('fullData.json') as dataJson:
    data = json.load(dataJson)

In [401]:
df_data = pd.DataFrame(data)
df = df_data[df_data['session'].notna()]

In [402]:
#get all events which are actually in TestSchwer
array_input_schwer = ['inputHobby','inputCancelor','inputTemperature','inputDays','inputRiver', 'inputDifficultQuestion', 'clickHere', 'buttonYes', 'alibiClick']

df_einfach_without_schwerInput = df[~df['elementId'].isin(array_input_schwer)]
df_schwer_without_einfachInput = df[df['elementId'].isin(array_input_schwer)]

df_actually_schwer = df_einfach_without_schwerInput.loc[df_einfach_without_schwerInput['siteName'] == 'TestSchwer']
df_easy = df_actually_schwer.assign(sitename='TestSchwer')

df_einfach = df_einfach_without_schwerInput.loc[~(df_einfach_without_schwerInput['siteName'] == 'TestSchwer')]
df_schwer = pd.concat([df_easy, df_schwer_without_einfachInput])

pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)

In [403]:
#Gleich viele sessions bei TestSchwer und TestEinfach
sessionIdSchwer = df_schwer['session']
sessionIdEinfach = df_einfach['session']

df_einfach['is_duplicated'] = df_einfach.duplicated('session')
#86 ids auf Seite Einfach
setEinfach = set(sessionIdEinfach)
length = len(setEinfach)

#59 ids auf Seite Schwer
df_schwer['is_duplicated'] = df_schwer.duplicated('session')
setSchwer = set(sessionIdSchwer)
lengthSchwer = len(setSchwer)

in_schwer_but_not_in_einfach = setSchwer - setEinfach
in_einfach_but_not_in_schwer = setEinfach - setSchwer

array_einfach = list(in_einfach_but_not_in_schwer)
array_schwer = list(in_schwer_but_not_in_einfach)

#66 Teilnehmer bzw. Sessions?
df_einfach_without_ids = df_einfach[~df_einfach['session'].isin(array_einfach)]
df_schwer_without_ids = df_schwer[~df_schwer['session'].isin(array_schwer)]

df_einfach_final = df_einfach_without_ids.drop(['clientId', 'is_duplicated'], axis=1)
df_schwer_final = df_schwer_without_ids.drop(['clientId', 'is_duplicated'], axis=1)

<ipython-input-403-7d7ef3e23dfd>:5: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_einfach['is_duplicated'] = df_einfach.duplicated('session')


In [404]:
#save dataframe to file 
df_einfach_final.to_pickle('einfach.pkl') 
df_schwer_final.to_pickle('schwer.pkl')

In [405]:
df1 = pd.read_pickle('einfach.pkl') 

In [406]:
df_einfach = pd.read_pickle('einfach.pkl') 
df_schwer = pd.read_pickle('schwer.pkl') 

df_data = pd.concat([df_einfach, df_schwer])
df = shuffle(df_data)

#remove scroll
df_data_without_scroll = df.loc[df["type"] !="scroll"]

In [407]:
# new sessionId 
from random import random
from secrets import choice

array_of_ids = df_data_without_scroll['session'].value_counts().index.tolist()

random_numbers_ids = np.random.randint(101,1000,size=len(array_of_ids))

df_data_without_scroll['session'] = df_data_without_scroll['session'].replace(array_of_ids, random_numbers_ids)

df_data_without_scroll = df_data_without_scroll.drop(['sitename', 'browser', 'key'], axis=1)

df_data_without_scroll.head()

<ipython-input-407-d0db9dcc5289>:9: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_data_without_scroll['session'] = df_data_without_scroll['session'].replace(array_of_ids, random_numbers_ids)


elementId           timeStamp       type    siteName  \
6518         inputHobby                7733   mouseout  TestSchwer   
27960     inputCancelor            526677.5   mouseout  TestSchwer   
9469         inputRiver  151131.90000000596   mouseout  TestSchwer   
6387         inputRiver              546755  mouseover  TestSchwer   
12470  inputTemperature              452687  mouseover  TestSchwer   

                           date clientX clientY  session height width  
6518   2022-10-18T14:31:09.333Z     869     443      538    962  1724  
27960  2022-10-22T07:45:20.042Z     238     357      795    661   360  
9469   2022-10-19T06:34:23.947Z     613     579      601   1336  1720  
6387   2022-10-18T14:18:23.118Z     857     569      854   1328  2560  
12470  2022-10-19T07:06:09.166Z     231     457      400    967  1291

In [408]:
#replace values of columns 
df_data_without_scroll['siteName'] = df_data_without_scroll['siteName'].replace('TestEinfach', 0)
df_data_without_scroll['siteName'] = df_data_without_scroll['siteName'].replace('TestSchwer', 1)

In [409]:
#set date as float
df_data_without_scroll['real_date'] = df_data_without_scroll['date'].astype('datetime64[ns]')
df_data_without_scroll['real_date'] = (df_data_without_scroll['real_date'] - df_data_without_scroll['real_date'].min())  / np.timedelta64(1,'D')
df_data_without_scroll = df_data_without_scroll.drop(['date'], axis=1)

In [410]:
#change types as int
array_of_type = df_data_without_scroll['type'].value_counts().index.tolist()
array_of_value_type = [510, 511, 512, 513, 514, 515]

In [411]:
def changeFields(ids, types, value): 
    df_data_without_scroll[ids] = df_data_without_scroll[ids].replace(types, value)

for index, item in enumerate(array_of_type):
    changeFields('type', array_of_type[index], array_of_value_type[index])

In [412]:
array_of_elementIds = df_data_without_scroll['elementId'].value_counts().index.tolist()
array_of_value_elementIds = list(range(11, 28))

for index, item in enumerate(array_of_elementIds):
    changeFields('elementId', array_of_elementIds[index], array_of_value_elementIds[index])

In [413]:
df_data_without_scroll['timeStamp'] = df_data_without_scroll['timeStamp'].astype(float)
df_data_without_scroll['clientX'] = df_data_without_scroll['clientX'].astype(float)
df_data_without_scroll['clientY'] = df_data_without_scroll['clientX'].astype(float)
df_data_without_scroll['height'] = df_data_without_scroll['height'].astype(float)

In [414]:
df_data_without_scroll["clientY"] = df_data_without_scroll["clientY"].fillna(df_data_without_scroll["clientY"].mean())
df_data_without_scroll["clientX"] = df_data_without_scroll["clientX"].fillna(df_data_without_scroll["clientX"].mean())

In [415]:
df_data_without_scroll.reset_index(inplace=True)
df_data_without_scroll.drop(['index'], axis=1)

elementId  timeStamp  type  siteName      clientX      clientY  session  \
0            13     7733.0   511         1   869.000000   869.000000      538   
1            14   526677.5   511         1   238.000000   238.000000      795   
2            12   151131.9   511         1   613.000000   613.000000      601   
3            12   546755.0   510         1   857.000000   857.000000      854   
4            11   452687.0   510         1   231.000000   231.000000      400   
5            11   488542.4   514         0   614.857006   614.857006      538   
6            12   267703.5   511         1   418.000000   418.000000      755   
7            14    19040.0   512         1   614.857006   614.857006      327   
8            11   157081.5   513         1   614.857006   614.857006      755   
9            13    19057.0   510         1   698.000000   698.000000      897   
10           16   303972.6   510         1   956.000000   956.000000      721   
11           13    25470.0   511         1   882.000000   882.000000      854   
12           21    22266.1   512         0   614.857006   614.857006      178   
13           22     5665.0   510         0   293.000000   293.000000      768   
14           16    30286.0   512         1   614.857006   614.857006      214   
15           14    14860.3   512         1   614.857006   614.857006      390   
16           18     1603.0   511         0   623.000000   623.000000      896   
17           13    25437.5   510         1   770.000000   770.000000      688   
18           11   172703.6   514         0   614.857006   614.857006      796   
19           11   492507.9   511         1   999.000000   999.000000      854   
20           11    80983.5   514         0   614.857006   614.857006      390   
21           12   146206.8   511         1   633.000000   633.000000      695   
22           24    18867.7   512         0   614.857006   614.857006      800   
23           19   502702.9   513         1   614.857006   614.857006      795   
24           18    11411.0   510         0   198.000000   198.000000      613   
25           20    17851.0   512         0   614.857006   614.857006      820   
26           18     1082.0   510         0   306.000000   306.000000      103   
27           11   233613.0   513         1   614.857006   614.857006      843   
28           11   225818.9   510         1   467.000000   467.000000      783   
29           12   134847.0   511         1   659.000000   659.000000      897   
30           23    20851.4   512         0   614.857006   614.857006      854   
31           11   371462.1   512         1   614.857006   614.857006      178   
32           12   119475.0   511         1   238.000000   238.000000      613   
33           20      850.0   510         0   633.000000   633.000000      110   
34           17   146964.3   513         1   614.857006   614.857006      854   
35           14    24472.4   512         1   614.857006   614.857006      460   
36           23    12659.0   510         0   245.000000   245.000000      552   
37           14   106299.1   512         1   614.857006   614.857006      688   
38           12    39811.8   514         0   614.857006   614.857006      796   
39           14    73928.6   511         1   871.000000   871.000000      755   
40           19   112896.0   513         1   614.857006   614.857006      314   
41           20    13156.0   511         0  1150.000000  1150.000000      178   
42           18     2395.0   513         0   614.857006   614.857006      402   
43           17     1745.0   512         1   614.857006   614.857006      152   
44           18     7766.0   511         0   305.000000   305.000000      268   
45           23    21042.0   513         0   614.857006   614.857006      613   
46           22     8949.0   513         0   614.857006   614.857006      314   
47           12    32858.0   511         1   489.000000   489.000000      330   
48           18     7056.0   514     

In [416]:
df_data_without_scroll.to_pickle('fullCleanedData.pkl') 